DENSE RETRIEVAL

In [1]:
!pip install -U beir

     |████████████████████████████████| 52 kB 822 kB/s 
     |████████████████████████████████| 78 kB 5.6 MB/s 
     |████████████████████████████████| 8.4 MB 43.3 MB/s 
     |████████████████████████████████| 378 kB 71.8 MB/s 
     |████████████████████████████████| 4.4 MB 55.2 MB/s 
     |████████████████████████████████| 3.1 MB 58.8 MB/s 
     |████████████████████████████████| 3.3 MB 64.7 MB/s 
     |████████████████████████████████| 1.2 MB 74.1 MB/s 
     |████████████████████████████████| 59 kB 8.6 MB/s 
     |████████████████████████████████| 596 kB 72.0 MB/s 
     |████████████████████████████████| 895 kB 60.0 MB/s 
  Created wheel for beir: filename=beir-0.2.3-py3-none-any.whl size=45805 sha256=e9836059a2d277a0c5f8ede670704035a10353d101cbc698fdd269285b32245f
  Stored in directory: /root/.cache/pip/wheels/af/29/4c/261c842753d34921b8b35c1b8679720114f8536654767430dd
  Created wheel for pytrec-eval: filename=pytrec_eval-0.5-cp37-cp37m-linux_x86_64.whl size=263964 sha256=861170e78e

In [2]:
import pathlib, os
import time
import pandas as pd
import random
import requests
import json
import torch
import torch.multiprocessing as mp
from tqdm.notebook import tqdm
from tqdm.autonotebook import trange
from beir import util, LoggingHandler
from beir.retrieval.evaluation import EvaluateRetrieval
from beir.retrieval import models
from beir.retrieval.search.dense import DenseRetrievalExactSearch as DRES
from beir.datasets.data_loader import GenericDataLoader

In [3]:
def load(dataset):
  hostname = 'localhost'
  index_name = dataset
  url = 'https://public.ukp.informatik.tu-darmstadt.de/thakur/BEIR/datasets/{}.zip'.format(dataset)
  out_dir = os.path.join(os.getcwd(), 'datasets')
  data_path = util.download_and_unzip(url, out_dir)
  return GenericDataLoader(data_path).load(split='test') # 'test', 'train', 'dev'


In [4]:
def retrieve(corpus, queries, qrels, model_name, batch_size, score_function):
  if batch_size is None:
    dr_model = EvaluateRetrieval(DRES(models.SentenceBERT(model_name)), score_function=score_function)
  else:
    dr_model = EvaluateRetrieval(
        DRES(models.SentenceBERT(model_name), batch_size=batch_size), score_function=score_function)
  res_model = dr_model.retrieve(corpus, queries)
  return dr_model.evaluate(qrels, res_model, dr_model.k_values)

In [5]:
def evaluate(corpus, queries, qrels, model_name, batch_size, score_function):
  ndcg, _map, recall, precision = retrieve(corpus, queries, qrels, model_name, batch_size, score_function)
  c_map = 'MAP@10'
  c_map_h = 'MAP@100'
  c_map_t = 'MAP@1000'
  c_ndcg = 'NDCG@10'
  c_ndcg_h = 'NDCG@100'
  c_ndcg_t = 'NDCG@1000'
  c_pre = 'P@10'
  c_pre_h = 'P@100'
  c_pre_t = 'P@1000'
  c_rec = 'Recall@10'
  c_rec_h = 'Recall@100'
  c_rec_t = 'Recall@1000'
  eval_dict = {
      c_map: [_map[c_map]], 
      c_map_h: [_map[c_map_h]],
      c_map_t: [_map[c_map_t]],
      c_ndcg: [ndcg[c_ndcg]], 
      c_ndcg_h: [ndcg[c_ndcg_h]],
      c_ndcg_t: [ndcg[c_ndcg_t]],
      c_pre: [precision[c_pre]], 
      c_pre_h: [precision[c_pre_h]],
      c_pre_t: [precision[c_pre_t]],
      c_rec: [recall[c_rec]],
      c_rec_h: [recall[c_rec_h]],
      c_rec_t: [recall[c_rec_t]]}
  eval_df = pd.DataFrame(data=eval_dict)
  eval_df.index = [model_name]
  return eval_df

In [6]:
cv_corpus, cv_queries, cv_qrels = load('trec-covid')
cv_als = evaluate(cv_corpus, cv_queries, cv_qrels, 'allenai-specter', 128, 'dot')
cv_amp = evaluate(cv_corpus, cv_queries, cv_qrels, 'all-mpnet-base-v2', 128, 'dot')
cv_adr = evaluate(cv_corpus, cv_queries, cv_qrels, 'all-distilroberta-v1', 128, 'dot')
cv_aml = evaluate(cv_corpus, cv_queries, cv_qrels, 'all-MiniLM-L12-v2', 128, 'dot')
cv_mmp = evaluate(cv_corpus, cv_queries, cv_qrels, 'multi-qa-mpnet-base-dot-v1', 128, 'dot')
cv_mml = evaluate(cv_corpus, cv_queries, cv_qrels, 'multi-qa-MiniLM-L6-cos-v1', 128, 'cos_sim')
cv_mdd = evaluate(cv_corpus, cv_queries, cv_qrels, 'multi-qa-distilbert-dot-v1', 128, 'dot')
cv_mdc = evaluate(cv_corpus, cv_queries, cv_qrels, 'multi-qa-distilbert-cos-v1', 128, 'cos_sim')
cv_msdd = evaluate(cv_corpus, cv_queries, cv_qrels, 'msmarco-distilbert-base-tas-b', 128, 'dot')
cv_msdc = evaluate(cv_corpus, cv_queries, cv_qrels, 'msmarco-distilbert-dot-v5', 128, 'dot')
cv_msbc = evaluate(cv_corpus, cv_queries, cv_qrels, 'msmarco-bert-co-condensor', 128, 'dot')
cv_msra = evaluate(cv_corpus, cv_queries, cv_qrels, 'msmarco-roberta-base-ance-firstp', None, 'dot')

/content/datasets/trec-covid.zip:   0%|          | 0.00/70.5M [00:00<?, ?iB/s]

  0%|          | 0/171332 [00:00<?, ?it/s]

Downloading:   0%|          | 0.00/690 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.71k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/622 [00:00<?, ?B/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/167 [00:00<?, ?it/s]

In [7]:
sf_corpus, sf_queries, sf_qrels = load('scifact')
sf_als = evaluate(sf_corpus, sf_queries, sf_qrels, 'allenai-specter', 128, 'dot')
sf_amp = evaluate(sf_corpus, sf_queries, sf_qrels, 'all-mpnet-base-v2', 128, 'dot')
sf_adr = evaluate(sf_corpus, sf_queries, sf_qrels, 'all-distilroberta-v1', 128, 'dot')
sf_aml = evaluate(sf_corpus, sf_queries, sf_qrels, 'all-MiniLM-L12-v2', 128, 'dot')
sf_mmp = evaluate(sf_corpus, sf_queries, sf_qrels, 'multi-qa-mpnet-base-dot-v1', 128, 'dot')
sf_mml = evaluate(sf_corpus, sf_queries, sf_qrels, 'multi-qa-MiniLM-L6-cos-v1', 128, 'cos_sim')
sf_mdd = evaluate(sf_corpus, sf_queries, sf_qrels, 'multi-qa-distilbert-dot-v1', 128, 'dot')
sf_mdc = evaluate(sf_corpus, sf_queries, sf_qrels, 'multi-qa-distilbert-cos-v1', 128, 'cos_sim')
sf_msdd = evaluate(sf_corpus, sf_queries, sf_qrels, 'msmarco-distilbert-base-tas-b', 128, 'dot')
sf_msdc = evaluate(sf_corpus, sf_queries, sf_qrels, 'msmarco-distilbert-dot-v5', 128, 'dot')
sf_msbc = evaluate(sf_corpus, sf_queries, sf_qrels, 'msmarco-bert-co-condensor', 128, 'dot')
sf_msra = evaluate(sf_corpus, sf_queries, sf_qrels, 'msmarco-roberta-base-ance-firstp', None, 'dot')

/content/datasets/scifact.zip:   0%|          | 0.00/2.69M [00:00<?, ?iB/s]

  0%|          | 0/5183 [00:00<?, ?it/s]

Batches:   0%|          | 0/3 [00:00<?, ?it/s]

Batches:   0%|          | 0/41 [00:00<?, ?it/s]

Batches:   0%|          | 0/3 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/41 [00:00<?, ?it/s]

Batches:   0%|          | 0/3 [00:00<?, ?it/s]

Batches:   0%|          | 0/41 [00:00<?, ?it/s]

Batches:   0%|          | 0/3 [00:00<?, ?it/s]

Batches:   0%|          | 0/41 [00:00<?, ?it/s]

In [8]:
sd_corpus, sd_queries, sd_qrels = load('scidocs')
sd_als = evaluate(sd_corpus, sd_queries, sd_qrels, 'allenai-specter', 128, 'dot')
sd_amp = evaluate(sd_corpus, sd_queries, sd_qrels, 'all-mpnet-base-v2', 128, 'dot')
sd_adr = evaluate(sd_corpus, sd_queries, sd_qrels, 'all-distilroberta-v1', 128, 'dot')
sd_aml = evaluate(sd_corpus, sd_queries, sd_qrels, 'all-MiniLM-L12-v2', 128, 'dot')
sd_mmp = evaluate(sd_corpus, sd_queries, sd_qrels, 'multi-qa-mpnet-base-dot-v1', 128, 'dot')
sd_mml = evaluate(sd_corpus, sd_queries, sd_qrels, 'multi-qa-MiniLM-L6-cos-v1', 128, 'cos_sim')
sd_mdd = evaluate(sd_corpus, sd_queries, sd_qrels, 'multi-qa-distilbert-dot-v1', 128, 'dot')
sd_mdc = evaluate(sd_corpus, sd_queries, sd_qrels, 'multi-qa-distilbert-cos-v1', 128, 'cos_sim')
sd_msdd = evaluate(sd_corpus, sd_queries, sd_qrels, 'msmarco-distilbert-base-tas-b', 128, 'dot')
sd_msdc = evaluate(sd_corpus, sd_queries, sd_qrels, 'msmarco-distilbert-dot-v5', 128, 'dot')
sd_msbc = evaluate(sd_corpus, sd_queries, sd_qrels, 'msmarco-bert-co-condensor', 128, 'dot')
sd_msra = evaluate(sd_corpus, sd_queries, sd_qrels, 'msmarco-roberta-base-ance-firstp', None, 'dot')

/content/datasets/scidocs.zip:   0%|          | 0.00/136M [00:00<?, ?iB/s]

  0%|          | 0/25657 [00:00<?, ?it/s]

Batches:   0%|          | 0/8 [00:00<?, ?it/s]

Batches:   0%|          | 0/201 [00:00<?, ?it/s]

Batches:   0%|          | 0/8 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/201 [00:00<?, ?it/s]

Batches:   0%|          | 0/8 [00:00<?, ?it/s]

Batches:   0%|          | 0/201 [00:00<?, ?it/s]

Batches:   0%|          | 0/8 [00:00<?, ?it/s]

Batches:   0%|          | 0/201 [00:00<?, ?it/s]

In [9]:
nf_corpus, nf_queries, nf_qrels = load('nfcorpus')
nf_als = evaluate(nf_corpus, nf_queries, nf_qrels, 'allenai-specter', 128, 'dot')
nf_amp = evaluate(nf_corpus, nf_queries, nf_qrels, 'all-mpnet-base-v2', 128, 'dot')
nf_adr = evaluate(nf_corpus, nf_queries, nf_qrels, 'all-distilroberta-v1', 128, 'dot')
nf_aml = evaluate(nf_corpus, nf_queries, nf_qrels, 'all-MiniLM-L12-v2', 128, 'dot')
nf_mmp = evaluate(nf_corpus, nf_queries, nf_qrels, 'multi-qa-mpnet-base-dot-v1', 128, 'dot')
nf_mml = evaluate(nf_corpus, nf_queries, nf_qrels, 'multi-qa-MiniLM-L6-cos-v1', 128, 'cos_sim')
nf_mdd = evaluate(nf_corpus, nf_queries, nf_qrels, 'multi-qa-distilbert-dot-v1', 128, 'dot')
nf_mdc = evaluate(nf_corpus, nf_queries, nf_qrels, 'multi-qa-distilbert-cos-v1', 128, 'cos_sim')
nf_msdd = evaluate(nf_corpus, nf_queries, nf_qrels, 'msmarco-distilbert-base-tas-b', 128, 'dot')
nf_msdc = evaluate(nf_corpus, nf_queries, nf_qrels, 'msmarco-distilbert-dot-v5', 128, 'dot')
nf_msbc = evaluate(nf_corpus, nf_queries, nf_qrels, 'msmarco-bert-co-condensor', 128, 'dot')
nf_msra = evaluate(nf_corpus, nf_queries, nf_qrels, 'msmarco-roberta-base-ance-firstp', None, 'dot')

/content/datasets/nfcorpus.zip:   0%|          | 0.00/2.34M [00:00<?, ?iB/s]

  0%|          | 0/3633 [00:00<?, ?it/s]

Batches:   0%|          | 0/3 [00:00<?, ?it/s]

Batches:   0%|          | 0/29 [00:00<?, ?it/s]

Batches:   0%|          | 0/3 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/29 [00:00<?, ?it/s]

Batches:   0%|          | 0/3 [00:00<?, ?it/s]

Batches:   0%|          | 0/29 [00:00<?, ?it/s]

Batches:   0%|          | 0/3 [00:00<?, ?it/s]

Batches:   0%|          | 0/29 [00:00<?, ?it/s]



---



**TREC-COVID** - [Homepage](https://ir.nist.gov/covidSubmit/index.html) - [Paper](https://arxiv.org/abs/2005.04474)

In [10]:
pd.concat([cv_als, cv_amp, cv_adr, cv_aml, cv_mmp, cv_mml, cv_mdd, cv_mdc, cv_msdd, cv_msdc, cv_msbc, cv_msra])

MAP@10  MAP@100  ...  Recall@100  Recall@1000
allenai-specter                   0.00681  0.03082  ...     0.05737      0.25094
all-mpnet-base-v2                 0.01218  0.07061  ...     0.10596      0.42466
all-distilroberta-v1              0.01273  0.06912  ...     0.10308      0.41148
all-MiniLM-L12-v2                 0.01164  0.06048  ...     0.09122      0.34378
multi-qa-mpnet-base-dot-v1        0.01415  0.07601  ...     0.11257      0.40350
multi-qa-MiniLM-L6-cos-v1         0.01320  0.07010  ...     0.10412      0.37359
multi-qa-distilbert-dot-v1        0.01608  0.08088  ...     0.11218      0.39644
multi-qa-distilbert-cos-v1        0.01295  0.07276  ...     0.10592      0.38220
msmarco-distilbert-base-tas-b     0.01025  0.05286  ...     0.08563      0.32190
msmarco-distilbert-dot-v5         0.01536  0.07169  ...     0.10212      0.34116
msmarco-bert-co-condensor         0.01775  0.09038  ...     0.12470      0.43225
msmarco-roberta-base-ance-firstp  0.01448  0.06982  ...     0.10016      0.34228

[12 rows x 12 columns]



---



**SCIFACT** - [Homepage](https://allenai.org/data/scifact) - [Paper](https://arxiv.org/abs/2004.14974)

In [11]:
pd.concat([sf_als, sf_amp, sf_adr, sf_aml, sf_mmp, sf_mml, sf_mdd, sf_mdc, sf_msdd, sf_msdc, sf_msbc, sf_msra])

MAP@10  MAP@100  ...  Recall@100  Recall@1000
allenai-specter                   0.44783  0.45681  ...     0.85222      0.97500
all-mpnet-base-v2                 0.60827  0.61595  ...     0.94167      0.99667
all-distilroberta-v1              0.57580  0.58185  ...     0.92000      0.99667
all-MiniLM-L12-v2                 0.57186  0.57863  ...     0.91167      0.98333
multi-qa-mpnet-base-dot-v1        0.54151  0.54938  ...     0.86833      0.98667
multi-qa-MiniLM-L6-cos-v1         0.49919  0.50910  ...     0.88033      0.97667
multi-qa-distilbert-dot-v1        0.49725  0.50593  ...     0.88822      0.96667
multi-qa-distilbert-cos-v1        0.54929  0.55748  ...     0.88533      0.96933
msmarco-distilbert-base-tas-b     0.59916  0.60459  ...     0.89100      0.98333
msmarco-distilbert-dot-v5         0.55076  0.55811  ...     0.87033      0.95333
msmarco-bert-co-condensor         0.54942  0.55659  ...     0.92767      0.99000
msmarco-roberta-base-ance-firstp  0.46612  0.47324  ...     0.81867      0.95667

[12 rows x 12 columns]



---



**SCIDOCS** - [Homepage](https://allenai.org/data/scidocs) - [Paper](https://arxiv.org/abs/2004.07180)

In [12]:
pd.concat([sd_als, sd_amp, sd_adr, sd_aml, sd_mmp, sd_mml, sd_mdd, sd_mdc, sd_msdd, sd_msdc, sd_msbc, sd_msra])

MAP@10  MAP@100  ...  Recall@100  Recall@1000
allenai-specter                   0.08170  0.10040  ...     0.39858      0.74312
all-mpnet-base-v2                 0.14426  0.17180  ...     0.54997      0.82972
all-distilroberta-v1              0.13030  0.15713  ...     0.52075      0.80807
all-MiniLM-L12-v2                 0.13168  0.15766  ...     0.50598      0.79053
multi-qa-mpnet-base-dot-v1        0.09721  0.11263  ...     0.35492      0.60205
multi-qa-MiniLM-L6-cos-v1         0.09210  0.10629  ...     0.33848      0.57345
multi-qa-distilbert-dot-v1        0.09098  0.10745  ...     0.36245      0.60043
multi-qa-distilbert-cos-v1        0.09239  0.10910  ...     0.36423      0.60232
msmarco-distilbert-base-tas-b     0.08543  0.10013  ...     0.33462      0.56763
msmarco-distilbert-dot-v5         0.08077  0.09356  ...     0.30865      0.52810
msmarco-bert-co-condensor         0.08013  0.09277  ...     0.31172      0.53407
msmarco-roberta-base-ance-firstp  0.06951  0.08045  ...     0.26928      0.47900

[12 rows x 12 columns]



---



**NFCORPUS** - [Homepage](https://www.cl.uni-heidelberg.de/statnlpgroup/nfcorpus/) - [Paper](https://www.cl.uni-heidelberg.de/~riezler/publications/papers/ECIR2016.pdf)

In [13]:
pd.concat([nf_als, nf_amp, nf_adr, nf_aml, nf_mmp, nf_mml, nf_mdd, nf_mdc, nf_msdd, nf_msdc, nf_msbc, nf_msra])

MAP@10  MAP@100  ...  Recall@100  Recall@1000
allenai-specter                   0.05045  0.06838  ...     0.19321      0.53337
all-mpnet-base-v2                 0.12034  0.15675  ...     0.33853      0.66070
all-distilroberta-v1              0.09818  0.12841  ...     0.29631      0.61755
all-MiniLM-L12-v2                 0.11551  0.14938  ...     0.31049      0.63148
multi-qa-mpnet-base-dot-v1        0.11234  0.14053  ...     0.28526      0.60445
multi-qa-MiniLM-L6-cos-v1         0.10533  0.12970  ...     0.26636      0.57816
multi-qa-distilbert-dot-v1        0.11721  0.14259  ...     0.28252      0.58034
multi-qa-distilbert-cos-v1        0.10925  0.13540  ...     0.28703      0.59908
msmarco-distilbert-base-tas-b     0.11945  0.14587  ...     0.28012      0.58277
msmarco-distilbert-dot-v5         0.10836  0.13045  ...     0.26435      0.53429
msmarco-bert-co-condensor         0.11702  0.14415  ...     0.28486      0.61520
msmarco-roberta-base-ance-firstp  0.08060  0.09878  ...     0.23475      0.54672

[12 rows x 12 columns]

end of fun.